In [4]:
import gym
import numpy as np

MAX_NUM_EPISODES = 50000
STEPS_PER_EPISODE =  200
EPSILON_MIN = 0.005
max_num_steps = MAX_NUM_EPISODES *  STEPS_PER_EPISODE
EPSILON_DECAY = 500 * EPSILON_MIN / max_num_steps
ALPHA = 0.05
GAMMA = 0.98
NUM_DISCRETE_BINS = 30

class Q_Learner(object):
    def __init__(self, env):
        self.obs_shape = env.observation_space.shape
        self.obs_high = env.observation_space.high
        self.obs_low = env.observation_space.low
        self.obs_bins = NUM_DISCRETE_BINS
        self.bin_width = (self.obs_high - self.obs_low) / self.obs_bins
        self.action_shape = env.action_space.n
        self.Q = np.zeros((self.obs_bins + 1, self.obs_bins+1,
                          self.action_shape))
        self.alpha = ALPHA
        self.gamma = GAMMA
        self.epsilon = 1.0
        
    def discretize(self, obs):
        return tuple(((obs - self.obs_low) /  self.bin_width).astype(int))
    
    def get_action(self, obs):
        discretized_obs = self.discretize(obs)
        if self.epsilon > EPSILON_MIN:
            self.epsilon -= EPSILON_DECAY
        if np.random.random() > self.epsilon:
            return np.argmax(self.Q[discretized_obs])
        else:
            return np.random.choice([a for a in range(self.action_shape)])
        
    def learn(self, obs, action, reward, next_obs):
        discretized_obs = self.discretize(obs)
        discretized_next_obs = self.discretize(next_obs)
        td_target = reward + self.gamma * np.max(self.Q[discretized_next_obs])
        td_error = td_target - self.Q[discretized_obs][action]
        self.Q[discretized_obs][action] += self.alpha * td_error
        
        
def train(agent, env):
    best_reward = -float('inf')
    for episode in range(MAX_NUM_EPISODES):
        done = False
        obs = env.reset()
        total_reward = 0.0
        while not done:
            action = agent.get_action(obs)
            next_obs, reward, done, info = env.step(action)
            agent.learn(obs, action, reward, next_obs)
            obs = next_obs
            total_reward += reward
        if total_reward > best_reward:
            best_reward = total_reward
        print('Episode#:{} reward:{} best_reward:{} eps:{}'.format(episode,
                      total_reward, best_reward, agent.epsilon))
    return np.argmax(agent.Q, axis=2)


def test(agent, env, policy):
    done = False
    obs = env.reset()
    total_reward = 0.0
    while not done:
        action = policy[agent.discretize(obs)]
        next_obs, reward, done, info = env.step(action)
        obs = next_obs
        total_reward += reward
    return  total_reward

    
if __name__ == '__main__':
    env = gym.make('MountainCar-v0')
    agent = Q_Learner(env)
    learned_policy = train(agent, env)
    gym_monitor_path = './gym_monitor_output'
    env = gym.wrappers.Monitor(env, gym_monitor_path, force=True)
    for _ in range(1000):
        test(agent, env, learned_policy)
    env.close()

Episode#:0 reward:-200.0 best_reward:-200.0 eps:0.999949999999993
Episode#:1 reward:-200.0 best_reward:-200.0 eps:0.999899999999986
Episode#:2 reward:-200.0 best_reward:-200.0 eps:0.999849999999979
Episode#:3 reward:-200.0 best_reward:-200.0 eps:0.999799999999972
Episode#:4 reward:-200.0 best_reward:-200.0 eps:0.999749999999965
Episode#:5 reward:-200.0 best_reward:-200.0 eps:0.9996999999999581
Episode#:6 reward:-200.0 best_reward:-200.0 eps:0.9996499999999511
Episode#:7 reward:-200.0 best_reward:-200.0 eps:0.9995999999999441
Episode#:8 reward:-200.0 best_reward:-200.0 eps:0.9995499999999371
Episode#:9 reward:-200.0 best_reward:-200.0 eps:0.9994999999999301
Episode#:10 reward:-200.0 best_reward:-200.0 eps:0.9994499999999231
Episode#:11 reward:-200.0 best_reward:-200.0 eps:0.9993999999999161
Episode#:12 reward:-200.0 best_reward:-200.0 eps:0.9993499999999091
Episode#:13 reward:-200.0 best_reward:-200.0 eps:0.9992999999999022
Episode#:14 reward:-200.0 best_reward:-200.0 eps:0.999249999999

Episode#:130 reward:-200.0 best_reward:-200.0 eps:0.9934499999990845
Episode#:131 reward:-200.0 best_reward:-200.0 eps:0.9933999999990775
Episode#:132 reward:-200.0 best_reward:-200.0 eps:0.9933499999990705
Episode#:133 reward:-200.0 best_reward:-200.0 eps:0.9932999999990635
Episode#:134 reward:-200.0 best_reward:-200.0 eps:0.9932499999990565
Episode#:135 reward:-200.0 best_reward:-200.0 eps:0.9931999999990495
Episode#:136 reward:-200.0 best_reward:-200.0 eps:0.9931499999990425
Episode#:137 reward:-200.0 best_reward:-200.0 eps:0.9930999999990355
Episode#:138 reward:-200.0 best_reward:-200.0 eps:0.9930499999990285
Episode#:139 reward:-200.0 best_reward:-200.0 eps:0.9929999999990216
Episode#:140 reward:-200.0 best_reward:-200.0 eps:0.9929499999990146
Episode#:141 reward:-200.0 best_reward:-200.0 eps:0.9928999999990076
Episode#:142 reward:-200.0 best_reward:-200.0 eps:0.9928499999990006
Episode#:143 reward:-200.0 best_reward:-200.0 eps:0.9927999999989936
Episode#:144 reward:-200.0 best_re

Episode#:259 reward:-200.0 best_reward:-200.0 eps:0.9869999999981829
Episode#:260 reward:-200.0 best_reward:-200.0 eps:0.9869499999981759
Episode#:261 reward:-200.0 best_reward:-200.0 eps:0.9868999999981689
Episode#:262 reward:-200.0 best_reward:-200.0 eps:0.9868499999981619
Episode#:263 reward:-200.0 best_reward:-200.0 eps:0.9867999999981549
Episode#:264 reward:-200.0 best_reward:-200.0 eps:0.9867499999981479
Episode#:265 reward:-200.0 best_reward:-200.0 eps:0.986699999998141
Episode#:266 reward:-200.0 best_reward:-200.0 eps:0.986649999998134
Episode#:267 reward:-200.0 best_reward:-200.0 eps:0.986599999998127
Episode#:268 reward:-200.0 best_reward:-200.0 eps:0.98654999999812
Episode#:269 reward:-200.0 best_reward:-200.0 eps:0.986499999998113
Episode#:270 reward:-200.0 best_reward:-200.0 eps:0.986449999998106
Episode#:271 reward:-200.0 best_reward:-200.0 eps:0.986399999998099
Episode#:272 reward:-200.0 best_reward:-200.0 eps:0.986349999998092
Episode#:273 reward:-200.0 best_reward:-200

Episode#:388 reward:-200.0 best_reward:-200.0 eps:0.9805499999972813
Episode#:389 reward:-200.0 best_reward:-200.0 eps:0.9804999999972743
Episode#:390 reward:-200.0 best_reward:-200.0 eps:0.9804499999972673
Episode#:391 reward:-200.0 best_reward:-200.0 eps:0.9803999999972604
Episode#:392 reward:-200.0 best_reward:-200.0 eps:0.9803499999972534
Episode#:393 reward:-200.0 best_reward:-200.0 eps:0.9802999999972464
Episode#:394 reward:-200.0 best_reward:-200.0 eps:0.9802499999972394
Episode#:395 reward:-200.0 best_reward:-200.0 eps:0.9801999999972324
Episode#:396 reward:-200.0 best_reward:-200.0 eps:0.9801499999972254
Episode#:397 reward:-200.0 best_reward:-200.0 eps:0.9800999999972184
Episode#:398 reward:-200.0 best_reward:-200.0 eps:0.9800499999972114
Episode#:399 reward:-200.0 best_reward:-200.0 eps:0.9799999999972044
Episode#:400 reward:-200.0 best_reward:-200.0 eps:0.9799499999971975
Episode#:401 reward:-200.0 best_reward:-200.0 eps:0.9798999999971905
Episode#:402 reward:-200.0 best_re

Episode#:516 reward:-200.0 best_reward:-200.0 eps:0.9741499999963867
Episode#:517 reward:-200.0 best_reward:-200.0 eps:0.9740999999963798
Episode#:518 reward:-200.0 best_reward:-200.0 eps:0.9740499999963728
Episode#:519 reward:-200.0 best_reward:-200.0 eps:0.9739999999963658
Episode#:520 reward:-200.0 best_reward:-200.0 eps:0.9739499999963588
Episode#:521 reward:-200.0 best_reward:-200.0 eps:0.9738999999963518
Episode#:522 reward:-200.0 best_reward:-200.0 eps:0.9738499999963448
Episode#:523 reward:-200.0 best_reward:-200.0 eps:0.9737999999963378
Episode#:524 reward:-200.0 best_reward:-200.0 eps:0.9737499999963308
Episode#:525 reward:-200.0 best_reward:-200.0 eps:0.9736999999963238
Episode#:526 reward:-200.0 best_reward:-200.0 eps:0.9736499999963169
Episode#:527 reward:-200.0 best_reward:-200.0 eps:0.9735999999963099
Episode#:528 reward:-200.0 best_reward:-200.0 eps:0.9735499999963029
Episode#:529 reward:-200.0 best_reward:-200.0 eps:0.9734999999962959
Episode#:530 reward:-200.0 best_re

...

Episode#:49377 reward:-162.0 best_reward:-93.0 eps:0.0049999999486979654
Episode#:49378 reward:-140.0 best_reward:-93.0 eps:0.0049999999486979654
Episode#:49379 reward:-141.0 best_reward:-93.0 eps:0.0049999999486979654
Episode#:49380 reward:-156.0 best_reward:-93.0 eps:0.0049999999486979654
Episode#:49381 reward:-145.0 best_reward:-93.0 eps:0.0049999999486979654
Episode#:49382 reward:-142.0 best_reward:-93.0 eps:0.0049999999486979654
Episode#:49383 reward:-143.0 best_reward:-93.0 eps:0.0049999999486979654
Episode#:49384 reward:-152.0 best_reward:-93.0 eps:0.0049999999486979654
Episode#:49385 reward:-149.0 best_reward:-93.0 eps:0.0049999999486979654
Episode#:49386 reward:-163.0 best_reward:-93.0 eps:0.0049999999486979654
Episode#:49387 reward:-140.0 best_reward:-93.0 eps:0.0049999999486979654
Episode#:49388 reward:-140.0 best_reward:-93.0 eps:0.0049999999486979654
Episode#:49389 reward:-114.0 best_reward:-93.0 eps:0.0049999999486979654
Episode#:49390 reward:-153.0 best_reward:-93.0 eps:

Episode#:49504 reward:-143.0 best_reward:-93.0 eps:0.0049999999486979654
Episode#:49505 reward:-152.0 best_reward:-93.0 eps:0.0049999999486979654
Episode#:49506 reward:-145.0 best_reward:-93.0 eps:0.0049999999486979654
Episode#:49507 reward:-121.0 best_reward:-93.0 eps:0.0049999999486979654
Episode#:49508 reward:-147.0 best_reward:-93.0 eps:0.0049999999486979654
Episode#:49509 reward:-144.0 best_reward:-93.0 eps:0.0049999999486979654
Episode#:49510 reward:-140.0 best_reward:-93.0 eps:0.0049999999486979654
Episode#:49511 reward:-146.0 best_reward:-93.0 eps:0.0049999999486979654
Episode#:49512 reward:-122.0 best_reward:-93.0 eps:0.0049999999486979654
Episode#:49513 reward:-139.0 best_reward:-93.0 eps:0.0049999999486979654
Episode#:49514 reward:-138.0 best_reward:-93.0 eps:0.0049999999486979654
Episode#:49515 reward:-139.0 best_reward:-93.0 eps:0.0049999999486979654
Episode#:49516 reward:-151.0 best_reward:-93.0 eps:0.0049999999486979654
Episode#:49517 reward:-138.0 best_reward:-93.0 eps:

Episode#:49639 reward:-146.0 best_reward:-93.0 eps:0.0049999999486979654
Episode#:49640 reward:-115.0 best_reward:-93.0 eps:0.0049999999486979654
Episode#:49641 reward:-147.0 best_reward:-93.0 eps:0.0049999999486979654
Episode#:49642 reward:-114.0 best_reward:-93.0 eps:0.0049999999486979654
Episode#:49643 reward:-146.0 best_reward:-93.0 eps:0.0049999999486979654
Episode#:49644 reward:-139.0 best_reward:-93.0 eps:0.0049999999486979654
Episode#:49645 reward:-113.0 best_reward:-93.0 eps:0.0049999999486979654
Episode#:49646 reward:-139.0 best_reward:-93.0 eps:0.0049999999486979654
Episode#:49647 reward:-146.0 best_reward:-93.0 eps:0.0049999999486979654
Episode#:49648 reward:-153.0 best_reward:-93.0 eps:0.0049999999486979654
Episode#:49649 reward:-147.0 best_reward:-93.0 eps:0.0049999999486979654
Episode#:49650 reward:-137.0 best_reward:-93.0 eps:0.0049999999486979654
Episode#:49651 reward:-117.0 best_reward:-93.0 eps:0.0049999999486979654
Episode#:49652 reward:-145.0 best_reward:-93.0 eps:

Episode#:49775 reward:-111.0 best_reward:-93.0 eps:0.0049999999486979654
Episode#:49776 reward:-144.0 best_reward:-93.0 eps:0.0049999999486979654
Episode#:49777 reward:-140.0 best_reward:-93.0 eps:0.0049999999486979654
Episode#:49778 reward:-139.0 best_reward:-93.0 eps:0.0049999999486979654
Episode#:49779 reward:-141.0 best_reward:-93.0 eps:0.0049999999486979654
Episode#:49780 reward:-139.0 best_reward:-93.0 eps:0.0049999999486979654
Episode#:49781 reward:-144.0 best_reward:-93.0 eps:0.0049999999486979654
Episode#:49782 reward:-151.0 best_reward:-93.0 eps:0.0049999999486979654
Episode#:49783 reward:-143.0 best_reward:-93.0 eps:0.0049999999486979654
Episode#:49784 reward:-141.0 best_reward:-93.0 eps:0.0049999999486979654
Episode#:49785 reward:-115.0 best_reward:-93.0 eps:0.0049999999486979654
Episode#:49786 reward:-139.0 best_reward:-93.0 eps:0.0049999999486979654
Episode#:49787 reward:-138.0 best_reward:-93.0 eps:0.0049999999486979654
Episode#:49788 reward:-143.0 best_reward:-93.0 eps:

Episode#:49907 reward:-142.0 best_reward:-93.0 eps:0.0049999999486979654
Episode#:49908 reward:-149.0 best_reward:-93.0 eps:0.0049999999486979654
Episode#:49909 reward:-113.0 best_reward:-93.0 eps:0.0049999999486979654
Episode#:49910 reward:-142.0 best_reward:-93.0 eps:0.0049999999486979654
Episode#:49911 reward:-112.0 best_reward:-93.0 eps:0.0049999999486979654
Episode#:49912 reward:-135.0 best_reward:-93.0 eps:0.0049999999486979654
Episode#:49913 reward:-143.0 best_reward:-93.0 eps:0.0049999999486979654
Episode#:49914 reward:-109.0 best_reward:-93.0 eps:0.0049999999486979654
Episode#:49915 reward:-133.0 best_reward:-93.0 eps:0.0049999999486979654
Episode#:49916 reward:-141.0 best_reward:-93.0 eps:0.0049999999486979654
Episode#:49917 reward:-117.0 best_reward:-93.0 eps:0.0049999999486979654
Episode#:49918 reward:-142.0 best_reward:-93.0 eps:0.0049999999486979654
Episode#:49919 reward:-132.0 best_reward:-93.0 eps:0.0049999999486979654
Episode#:49920 reward:-138.0 best_reward:-93.0 eps: